In [20]:
import os
import sys
import nltk
import numpy as np
import string
import xml.etree.ElementTree as ET
from nltk.corpus import stopwords
from Sastrawi.Stemmer.StemmerFactory import StemmerFactory
from nltk.tag import CRFTagger
# np.set_printoptions(threshold=sys.maxsize)

def load_xml(path, size, start=0):
    list_xml = []

    # Loop each file in dir path
    for file in os.listdir(path):
        # Get absolute path
        fullname = os.path.join(path, file)
        
        # Parsing XML
        xml = ET.parse(fullname)
        
        # Append XMLTree into list_xml
        list_xml.append(xml)
    
    return list_xml[start:size+start]


def tokenization(list_xml):
    tokens = []

    # Loop each xml in list_xml
    for xml in list_xml:
        # Get text of tag <judul></judul> then remove punctuation
        judul = xml.find('judul').text.translate(str.maketrans('','',string.punctuation))
        
        # Get text of tag <kata_kunci></kata_kunci> then remove punctuation
        kata_kunci = xml.find('kata_kunci').text.translate(str.maketrans('','',string.punctuation))
        
        # Get text of tag <isi></isi> then remove punctuation
        isi = xml.find('isi').text.translate(str.maketrans('','',string.punctuation))
    
        # Append new tokens into current token (new tokens concat 3 tags with spaces)
        tokens = [*tokens, *nltk.word_tokenize(judul + " " + kata_kunci + " " + isi)]
    
    return tokens

def casefolding(tokens):
    # Case folding each token
    tokens = np.char.lower(tokens)
    return tokens


def remove_punctuation(tokens):
    # Punctuation symbols
    symbols = "!\"#$%&()*+-./:;<=>?@[\]^_`{|}~\n"
    
    # Iterate each punctuation symbol check if token contain punctuation symbol
    for i in range(len(symbols)):
        tokens = np.char.replace(tokens, symbols[i], '')
        tokens = np.char.replace(tokens, "  ", "")
    # Replace ',' with empty string
    tokens = np.char.replace(tokens, ',', '')
    
    return tokens

def remove_stopword(tokens):
    # Load stopwords into list_stopword
    list_stopword =  set(stopwords.words('indonesian'))
    new_tokens = []
    
    # Iterate each tokens. if token didn't match with stopword then append to new_tokens list
    for t in tokens:
        if t not in list_stopword:
            new_tokens.append(t)

    return new_tokens

def stemming(tokens):
    # Initialize stemmer
    factory = StemmerFactory()
    # Create stemmer
    stemmer = factory.create_stemmer()
    
    new_tokens = []
    # Iterate each tokens then apply stemming
    for t in tokens:
        new_tokens.append(stemmer.stem(t))
 
    return new_tokens

def post_tagging(tokens):
    # Create POS Tagger
    ct = CRFTagger()
    
    # Train Post tagger with all_indo_man_tag_corpus_model.crf.tagger data.
    ct.set_model_file('all_indo_man_tag_corpus_model.crf.tagger')
    
    # Do POS Tagging
    result = ct.tag_sents([tokens])
    return result

In [21]:
list_xml = load_xml('source', 999)
print(f"Total document:{len(list_xml)}")

Total document:401


In [22]:
tokens = tokenization(list_xml)
print(f"Total token:{len(tokens)}\n")
print(tokens)

Total token:119472

['Puji', 'Ekonomi', 'RI', 'IMF', 'Ramal', 'Pertumbuhan', 'Capai', '51', 'Persen', 'Ekonomi', 'Keuangan', 'Suku', 'Bunga', 'International', 'Monetary', 'Fund', 'IMF', 'memproyeksi', 'pertumbuhan', 'ekonomi', 'Indonesia', 'hingga', 'akhir', 'tahun', 'nanti', 'hanya', 'akan', 'mencapai', '5', 'persen', 'Namun', 'tahun', 'depan', 'pertumbuhannya', 'berpotensi', 'sedikit', 'menguat', 'hingga', 'tembus', '51', 'persen', 'Dewan', 'Eksekutif', 'IMF', 'Luis', 'E', 'Breuer', 'menyebut', 'perekonomian', 'Indonesia', 'terus', 'menunjukkan', 'perbaikan', 'Hal', 'ini', 'didukung', 'oleh', 'kebijakan', 'makroekonomi', 'yang', 'baik', 'serta', 'reformasi', 'struktural', 'yang', 'terus', 'berlanjut', 'Pemerintah', 'dan', 'otoritas', 'secara', 'terampil', 'mampu', 'melewati', 'tantangan', 'ekonomi', 'terkini', 'yang', 'tengah', 'melanda', 'ekonomi', 'global', 'Pertumbuhan', 'tetap', 'kuat', 'inflasi', 'menurun', 'secara', 'signifikan', 'defisit', 'transaksi', 'berjalan', 'tetap', 'te

In [23]:
tokens = casefolding(tokens)
print(f"Total token:{len(tokens)}\n")
print(tokens)

Total token:119472

['puji' 'ekonomi' 'ri' 'imf' 'ramal' 'pertumbuhan' 'capai' '51' 'persen'
 'ekonomi' 'keuangan' 'suku' 'bunga' 'international' 'monetary' 'fund'
 'imf' 'memproyeksi' 'pertumbuhan' 'ekonomi' 'indonesia' 'hingga' 'akhir'
 'tahun' 'nanti' 'hanya' 'akan' 'mencapai' '5' 'persen' 'namun' 'tahun'
 'depan' 'pertumbuhannya' 'berpotensi' 'sedikit' 'menguat' 'hingga'
 'tembus' '51' 'persen' 'dewan' 'eksekutif' 'imf' 'luis' 'e' 'breuer'
 'menyebut' 'perekonomian' 'indonesia' 'terus' 'menunjukkan' 'perbaikan'
 'hal' 'ini' 'didukung' 'oleh' 'kebijakan' 'makroekonomi' 'yang' 'baik'
 'serta' 'reformasi' 'struktural' 'yang' 'terus' 'berlanjut' 'pemerintah'
 'dan' 'otoritas' 'secara' 'terampil' 'mampu' 'melewati' 'tantangan'
 'ekonomi' 'terkini' 'yang' 'tengah' 'melanda' 'ekonomi' 'global'
 'pertumbuhan' 'tetap' 'kuat' 'inflasi' 'menurun' 'secara' 'signifikan'
 'defisit' 'transaksi' 'berjalan' 'tetap' 'terjaga' 'kondisi' 'ini' 'yang'
 'mampu' 'menopang' 'ekonomi' 'tahun' 'depan' 'ujar

In [24]:
tokens = remove_punctuation(tokens)
print(f"Total token:{len(tokens)}\n")
print(tokens)

Total token:119472

['puji' 'ekonomi' 'ri' 'imf' 'ramal' 'pertumbuhan' 'capai' '51' 'persen'
 'ekonomi' 'keuangan' 'suku' 'bunga' 'international' 'monetary' 'fund'
 'imf' 'memproyeksi' 'pertumbuhan' 'ekonomi' 'indonesia' 'hingga' 'akhir'
 'tahun' 'nanti' 'hanya' 'akan' 'mencapai' '5' 'persen' 'namun' 'tahun'
 'depan' 'pertumbuhannya' 'berpotensi' 'sedikit' 'menguat' 'hingga'
 'tembus' '51' 'persen' 'dewan' 'eksekutif' 'imf' 'luis' 'e' 'breuer'
 'menyebut' 'perekonomian' 'indonesia' 'terus' 'menunjukkan' 'perbaikan'
 'hal' 'ini' 'didukung' 'oleh' 'kebijakan' 'makroekonomi' 'yang' 'baik'
 'serta' 'reformasi' 'struktural' 'yang' 'terus' 'berlanjut' 'pemerintah'
 'dan' 'otoritas' 'secara' 'terampil' 'mampu' 'melewati' 'tantangan'
 'ekonomi' 'terkini' 'yang' 'tengah' 'melanda' 'ekonomi' 'global'
 'pertumbuhan' 'tetap' 'kuat' 'inflasi' 'menurun' 'secara' 'signifikan'
 'defisit' 'transaksi' 'berjalan' 'tetap' 'terjaga' 'kondisi' 'ini' 'yang'
 'mampu' 'menopang' 'ekonomi' 'tahun' 'depan' 'ujar

In [25]:
tokens = remove_stopword(tokens)
print(f"Total token:{len(tokens)}\n")
print(tokens)

Total token:76775

['puji', 'ekonomi', 'ri', 'imf', 'ramal', 'pertumbuhan', 'capai', '51', 'persen', 'ekonomi', 'keuangan', 'suku', 'bunga', 'international', 'monetary', 'fund', 'imf', 'memproyeksi', 'pertumbuhan', 'ekonomi', 'indonesia', 'mencapai', '5', 'persen', 'pertumbuhannya', 'berpotensi', 'menguat', 'tembus', '51', 'persen', 'dewan', 'eksekutif', 'imf', 'luis', 'e', 'breuer', 'menyebut', 'perekonomian', 'indonesia', 'perbaikan', 'didukung', 'kebijakan', 'makroekonomi', 'reformasi', 'struktural', 'berlanjut', 'pemerintah', 'otoritas', 'terampil', 'melewati', 'tantangan', 'ekonomi', 'terkini', 'melanda', 'ekonomi', 'global', 'pertumbuhan', 'kuat', 'inflasi', 'menurun', 'signifikan', 'defisit', 'transaksi', 'berjalan', 'terjaga', 'kondisi', 'menopang', 'ekonomi', 'breuer', 'keterangan', 'resminya', 'jumat', '2511', 'pertbreuer', 'konsumsi', 'rumah', 'tangga', 'indonesia', 'kuat', 'mendorong', 'pertumbuhan', 'ekonomi', '51', 'persen', 'samping', 'konsumsi', 'swasta', 'pertumbuhan',

In [26]:
tokens = stemming(tokens)
print(f"Total token:{len(tokens)}\n")
print(token)

Total token:73794

['puji', 'ekonomi', 'ri', 'imf', 'ramal', 'tumbuh', 'capai', '51', 'persen', 'ekonomi', 'uang', 'suku', 'bunga', 'international', 'monetary', 'fund', 'imf', 'proyeksi', 'tumbuh', 'ekonomi', 'indonesia', 'capai', '5', 'persen', 'tumbuh', 'potensi', 'kuat', 'tembus', '51', 'persen', 'dewan', 'eksekutif', 'imf', 'luis', 'e', 'breuer', 'ekonomi', 'indonesia', 'dukung', 'bijak', 'makroekonomi', 'reformasi', 'struktural', 'perintah', 'otoritas', 'terampil', 'tantang', 'ekonomi', 'landa', 'ekonomi', 'global', 'tumbuh', 'kuat', 'inflasi', 'turun', 'signifikan', 'defisit', 'transaksi', 'jalan', 'jaga', 'kondisi', 'topang', 'ekonomi', 'breuer', 'terang', 'resmi', 'jumat', '2511', 'pertbreuer', 'konsumsi', 'rumah', 'tangga', 'indonesia', 'kuat', 'dorong', 'tumbuh', 'ekonomi', '51', 'persen', 'samping', 'konsumsi', 'swasta', 'tumbuh', 'investasi', 'swasta', 'prediksi', 'rangkak', '2017', 'dorong', 'bangkit', 'harga', 'komoditas', 'perlahan', 'suku', 'bunga', 'perban', 'rendah', 

In [27]:
print(post_tagging(tokens))

[[('puji', 'VB'), ('ekonomi', 'NN'), ('ri', 'NN'), ('imf', 'NN'), ('ramal', 'JJ'), ('tumbuh', 'VB'), ('capai', 'VB'), ('51', 'CD'), ('persen', 'CD'), ('ekonomi', 'NN'), ('uang', 'NN'), ('suku', 'NN'), ('bunga', 'NN'), ('international', 'FW'), ('monetary', 'FW'), ('fund', 'FW'), ('imf', 'FW'), ('proyeksi', 'NN'), ('tumbuh', 'VB'), ('ekonomi', 'NN'), ('indonesia', 'NNP'), ('capai', 'VB'), ('5', 'CD'), ('persen', 'CD'), ('tumbuh', 'VB'), ('potensi', 'NN'), ('kuat', 'JJ'), ('tembus', 'VB'), ('51', 'CD'), ('persen', 'CD'), ('dewan', 'NN'), ('eksekutif', 'NN'), ('imf', 'FW'), ('luis', 'FW'), ('e', 'FW'), ('breuer', 'FW'), ('ekonomi', 'NN'), ('indonesia', 'NNP'), ('dukung', 'VB'), ('bijak', 'NN'), ('makroekonomi', 'NN'), ('reformasi', 'NN'), ('struktural', 'JJ'), ('perintah', 'NN'), ('otoritas', 'NN'), ('terampil', 'JJ'), ('tantang', 'VB'), ('ekonomi', 'NN'), ('landa', 'NN'), ('ekonomi', 'NN'), ('global', 'JJ'), ('tumbuh', 'VB'), ('kuat', 'JJ'), ('inflasi', 'NN'), ('turun', 'VB'), ('signifika

In [28]:
most_common_words = nltk.FreqDist(tokens)
print(most_common_words.most_common()[:10])

[('bunga', 2918), ('suku', 2553), ('bank', 1399), ('ekonomi', 1173), ('turun', 1147), ('persen', 1128), ('as', 1118), ('bi', 1003), ('fed', 856), ('the', 827)]
